## Import dependencies

Note: all sandbox endpoints currently read `https://a.mapillary.com/v3/graph` but will change to a v4 endpoint upon release

In [ ]:
import requests, json, math, mercantile, mapbox_vector_tile

## Define global variables

Note: get a client ID [here](https://www.mapillary.com/dashboard/developers), but you will generate a new one when v4 goes live

In [ ]:
client = 'YOUR_CLIENT_ID'
endpoint = 'https://a.mapillary.com/v3/graph'

user_keys = ['300001','300002']
image_keys = ['100001','100002']

## Retrieve an image by key with timestamp field

In [ ]:
image = image_keys[0]

request = 'https://a.mapillary.com/v3/graph/{}?client_id={}&fields={},{}'.format(image,client,'id','created_at')
response = requests.get(request, stream=True)
data = response.json()
print(data)

## Retrieve an image with multiple fields

In [ ]:
image = image_keys[0]
fields = ['id','altitude','atomic_scale','camera_parameter','camera_type','captured_at','compass_angle','created_at','created_by','geometry','height','image_url_2048']

request = 'https://a.mapillary.com/v3/graph/{}?client_id={}&fields={}'.format(image,client,','.join(fields))
response = requests.get(request, stream=True)
data = response.json()
print(data)

## Get multiple images with multiple fields

In [ ]:
fields = ['id','altitude','atomic_scale','camera_parameter','camera_type','captured_at','compass_angle','created_at','created_by','geometry','height','image_url_2048']

request = 'https://a.mapillary.com/v3/graph/images?ids={}&fields={}&client_id={}'.format(','.join(image_keys),','.join(fields),client)
response = requests.get(request, stream=True)
print(response.status_code)
data = response.json()
print(data)

## Retrieve all detections for an image

In [ ]:
image = image_keys[1]

request = 'https://a.mapillary.com/v3/graph/{}/detections?client_id={}'.format(image,client)
response = requests.get(request, stream=True)
print(response.status_code)
data = response.json()
print(data)

## Retrieve all detections with multiple fields for an image

In [ ]:
fields = ['key','id','value','geometry','image']

request = 'https://a.mapillary.com/v3/graph/{}/detections?fields={}&client_id={}'.format(image,','.join(fields),client)
response = requests.get(request, stream=True)
print(response.status_code)
data = response.json()
print(data)

## Get information about logged in user

In [ ]:
# generate a token with OAuth (will be updated for API v4)
# https://www.mapillary.com/developer/api-documentation/#oauth
mytoken = 'xyz123'

request = 'https://a.mapillary.com/v3/graph/me?client_id={}'.format(client)
response = requests.get(request, stream=True, headers={'Authorization: Bearer {}'.format(mytoken)})
print(response.status_code)
data = response.json()
print(data)

## Get list of organizations logged in user is within

In [ ]:
mytoken = 'xyz123'

request = 'https://a.mapillary.com/v3/graph/me/organizations?client_id={}'.format(client)
response = requests.get(request, stream=True, headers={'Authorization: Bearer {}'.format(mytoken)})
print(response.status_code)
data = response.json()
print(data)

## Retrieve tile with point query

see: https://github.com/mapbox/mercantile

In [ ]:
input_coords = [13.01765352487564,55.60817207168841]
zoom = 10
layers = ['images','sequences','map_features']

tile = mercantile.tile(input_coords[0],input_coords[1],zoom)
tile_url = 'https://a.mapillary.com/v3/graph/tiles/{}/{}/{}/{}.mvt?client_id={}'.format(layers[2],zoom,tile[0],tile[1],client)
print(tile_url)

## Retrieve tile with bbox query

see: https://github.com/mapbox/mercantile

In [ ]:
bbox = [12.995882034301758,55.59692277270469,13.039999008178711,55.62402228728622]
layers = ['images','sequences','map_features']

tile = mercantile.bounding_tile(bbox[0],bbox[1],bbox[2],bbox[3])
print(tile)
tile_url = 'https://a.mapillary.com/v3/graph/tiles/{}/{}/{}/{}.mvt?client_id={}'.format(layers[2],tile[2],tile[0],tile[1],client)
print(tile_url)

## Download all map features in a tile

see: https://github.com/tilezen/mapbox-vector-tile

In [47]:
zoom = 14
tileX = 8784
tileY = 5133
layers = ['images','sequences','map_features']
output = {"type": "FeatureCollection", "features": []}

tile_url = 'https://a.mapillary.com/v3/graph/tiles/{}/{}/{}/{}.mvt?client_id={}'.format(layers[0],zoom,tileX,tileY,client)
print(tile_url)

response = requests.get(tile_url)
print(response.status_code)
data = response.content
decoded_data = mapbox_vector_tile.decode(data)
output_layer = list(decoded_data.keys())[0]
output['features'] = decoded_data[output_layer]['features']

with open('output.geojson', 'w') as outfile:
    json.dump(output, outfile)

